In [1]:
import numpy as np
import pandas as pd
import pyomo.environ as pyo
from measure_optimize import MeasurementOptimizer, DataProcess, covariance_lib
import matplotlib.pyplot as plt
import pickle 

## Input Setting

### All measurements and index

- ads.gas_inlet.F (0)
- ads.gas_outlet.F (1)
- ads.gas_outlet.T (2)
- ads.gas_outlet.z (3)
- des.gas_inlet.F (4)
- des.gas_outlet.F (5)
- des.gas_outlet.T (6)
- des.gas_outlet.z (7)
- ads.T19 (8)
- ads.T23 (9)
- ads.T28 (10)
- ads.z19 (11)
- ads.z23 (12)
- ads.z28 (13)

One-time cost ones: 0,1,2, 4,5,6, 8,9,10

Time-cost ones: 3,7,11,12,13

Names in str: 'Ads.gas_inlet.F', 'Ads.gas_outlet.F', 'Ads.gas_outlet.T', 
             'Ads.gas_outlet.z("CO2")', 'Des.gas_inlet.F', 'Des.gas_outlet.F', 
             'Des.gas_outlet.T', 'Des.gas_outlet.z("CO2")', 'Ads.T_g.Value(19,10)', 
             'Ads.T_g.Value(23,10)', 'Ads.T_g.Value(28,10)', 'Ads.z("CO2",19,10)', 
             'Ads.z("CO2",23,10)', 'Ads.z("CO2",28,10)'

In [2]:
strategy3 = True

Nt =110

max_manual_num = 5 
min_interval_num = 10

In [3]:
if strategy3:
    static_ind = [0,1,2,3,4,5,6,7,8,9,10]
    dynamic_ind = [3,7,11,12,13]
    all_ind = static_ind+dynamic_ind

else:
    static_ind = [0,1,2,4,5,6,8,9,10]
    dynamic_ind = [3,7,11,12,13]

num_total = len(all_ind)

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 3, 7, 11, 12, 13]


In [4]:
all_names_strategy3 = ['Ads.gas_inlet.F', 'Ads.gas_outlet.F', 'Ads.gas_outlet.T', 
             'Des.gas_inlet.F', 'Des.gas_outlet.F', 
             'Des.gas_outlet.T',  'Ads.T_g.Value(19,10)', 
             'Ads.T_g.Value(23,10)', 'Ads.T_g.Value(28,10)', # all static
            'Ads.gas_outlet.z("CO2").static', 'Des.gas_outlet.z("CO2").static', # static z 
            'Ads.gas_outlet.z("CO2").dynamic', 'Des.gas_outlet.z("CO2").dynamic', # dynamic z 
            'Ads.z("CO2",19,10)', 'Ads.z("CO2",23,10)', 'Ads.z("CO2",28,10)']

In [5]:
if strategy3:
    static_cost = [1000, #ads.gas_inlet.F (0)
        1000, #ads.gas_outlet.F (1)
         500, #ads.gas_outlet.T (2)
        7000,
        1000, #des.gas_inlet.F (4)
        1000, #des.gas_outlet.F (5)
         500, #des.gas_outlet.T (6)
        7000,
         1000, #ads.T19 (8)
         1000, #ads.T23 (9)
         1000 #ads.T28 (10)
       ]
else:
    static_cost = [1000, #ads.gas_inlet.F (0)
        1000, #ads.gas_outlet.F (1)
         500, #ads.gas_outlet.T (2)
        1000, #des.gas_inlet.F (4)
        1000, #des.gas_outlet.F (5)
         500, #des.gas_outlet.T (6)
         1000, #ads.T19 (8)
         1000, #ads.T23 (9)
         1000 #ads.T28 (10)
       ]

static_cost.extend([100, 100, 500, 500, 500])

dynamic_cost = [0]*len(static_ind)
dynamic_cost.extend([100]*len(dynamic_ind))

max_manual = [max_manual_num]*num_total
min_time_interval = [min_interval_num]*num_total

In [24]:
print(sum(static_cost))

23700


In [6]:
measure_info = pd.DataFrame({
    "name": all_names_strategy3,
    "Q_index": all_ind,
        "static_cost": static_cost,
    "dynamic_cost": dynamic_cost,
    "min_time_interval": min_time_interval, 
    "max_manual_number": max_manual
})

print(measure_info)

                               name  Q_index  static_cost  dynamic_cost  \
0                   Ads.gas_inlet.F        0         1000             0   
1                  Ads.gas_outlet.F        1         1000             0   
2                  Ads.gas_outlet.T        2          500             0   
3                   Des.gas_inlet.F        3         7000             0   
4                  Des.gas_outlet.F        4         1000             0   
5                  Des.gas_outlet.T        5         1000             0   
6              Ads.T_g.Value(19,10)        6          500             0   
7              Ads.T_g.Value(23,10)        7         7000             0   
8              Ads.T_g.Value(28,10)        8         1000             0   
9    Ads.gas_outlet.z("CO2").static        9         1000             0   
10   Des.gas_outlet.z("CO2").static       10         1000             0   
11  Ads.gas_outlet.z("CO2").dynamic        3          100           100   
12  Des.gas_outlet.z("CO2

In [7]:
dataObject = DataProcess()
dataObject.read_jaco('./RotaryBed/Q'+str(Nt)+'_scale.csv')
Q = dataObject.get_Q_list(measure_info, Nt)


(16, 110, 5)


In [8]:
calculator = MeasurementOptimizer(Q, measure_info, error_opt=covariance_lib.mode0, verbose=True)

fim_expect = calculator.fim_computation()

print(np.shape(calculator.fim_collection))

(314721, 5, 5)


### Debug functions: check each unit FIM

In [9]:
def check(fim_set):
    for i in range(num_total):
        for j in range(num_total):
            fim = fim_set[i*num_total+j]
            if np.any(fim):
                logdet = np.log(np.linalg.det(fim))
                if logdet < 0:
                    print("unit FIM with small Det: ", i, j, ', logdet:', logdet)
                if max(np.linalg.eigvals(fim))/min(np.linalg.eigvals(fim)) > 1000:
                    print("unit FIM with big condition number:", i, j, ", eigvals:", np.linalg.eigvals(fim))

In [10]:
def print_fim(t):
    fim = calculator.fim_collection[t*num_total+t]
    print(fim)
    print(np.linalg.eigvals(fim))

total_fim = np.zeros((5,5))
for i in range(314721):
    total_fim += calculator.fim_collection[i]
print(total_fim)

[[ 5.68675822e+03  3.40446058e+00 -4.12615577e+03  1.12130355e+04
  -6.89977591e+02]
 [ 3.40446058e+00  5.76986520e+00  7.18420470e+00  6.82874325e+01
  -1.97005732e+01]
 [-4.12615577e+03  7.18420470e+00  3.34118481e+03 -8.54865956e+03
   1.50792220e+02]
 [ 1.12130355e+04  6.82874325e+01 -8.54865956e+03  2.60398825e+04
  -1.23576756e+03]
 [-6.89977591e+02 -1.97005732e+01  1.50792220e+02 -1.23576756e+03
   6.81552017e+02]]


### Initialize

In [11]:
num_static = len(static_ind)
num_dynamic  = len(dynamic_ind)
num_total = num_static + num_dynamic*Nt

In [68]:
with open('Mar31_D_110_25400', 'rb') as f:
    x = pickle.load(f)
    
print(x)

init_cov_y = x.copy()

for i in range(11):
    init_cov_y[i,i] = 1
    
# initialize all decisions
#init_cov_y = np.ones(x.shape) 

[[1. 1. 1. ... 0. 0. 0.]
 [1. 1. 1. ... 0. 0. 0.]
 [1. 1. 1. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]


In [69]:
#with open('strategy3_all_covy', 'rb') as f:
with open('Mar31_FIM_D_110_25400', 'rb') as f:
    fim_prior = pickle.load(f)
    
print(fim_prior)

[[ 5.55250465e+03 -2.60176025e+00 -4.14144936e+03  1.09884918e+04
  -5.00364270e+02]
 [-2.60176025e+00  5.21565817e+00  7.72472967e+00  5.02791472e+01
  -1.05238443e+01]
 [-4.14144936e+03  7.72472967e+00  3.32532473e+03 -8.52000771e+03
   1.66414816e+02]
 [ 1.09884918e+04  5.02791472e+01 -8.52000771e+03  2.52461208e+04
  -8.96319334e+02]
 [-5.00364270e+02 -1.05238443e+01  1.66414816e+02 -8.96319334e+02
   3.78313554e+02]]


In [84]:

mip_option = False
objective = "D"
sparse_opt = True
fix_opt = False

manual_num = 20
budget_opt = 25000

num_dynamic_time = np.linspace(2,220,Nt)

dynamic_time_dict = {}
for i, tim in enumerate(num_dynamic_time):
    dynamic_time_dict[i] = tim 

In [85]:
mod = calculator.continuous_optimization(mixed_integer=mip_option, 
                      obj=objective, 
                    fix=fix_opt, 
                    sparse=sparse_opt, 
                    num_dynamic_t_name = num_dynamic_time, 
                    manual_number = manual_num, 
                    budget=budget_opt,
                    init_cov_y= init_cov_y, 
                    initial_fim = fim_prior)

mod = calculator.solve(mod, mip_option=mip_option, objective = objective)

{'ele_0_0': 5552.504645257687, 'ele_0_1': -2.6017602457652953, 'ele_0_2': -4141.449357723191, 'ele_0_3': 10988.491791875163, 'ele_0_4': -500.3642698921787, 'ele_1_1': 5.215658165681418, 'ele_1_2': 7.724729673702201, 'ele_1_3': 50.2791472159897, 'ele_1_4': -10.523844298809584, 'ele_2_2': 3325.32472544561, 'ele_2_3': -8520.007707566137, 'ele_2_4': 166.4148155968816, 'ele_3_3': 25246.12078642519, 'ele_3_4': -896.3193341158011, 'ele_4_4': 378.3135537330606}
initialize with: {'ele_0_0': 5552.504645257687, 'ele_0_1': -2.6017602457652953, 'ele_0_2': -4141.449357723191, 'ele_0_3': 10988.491791875163, 'ele_0_4': -500.3642698921787, 'ele_1_1': 5.215658165681418, 'ele_1_2': 7.724729673702201, 'ele_1_3': 50.2791472159897, 'ele_1_4': -10.523844298809584, 'ele_2_2': 3325.32472544561, 'ele_2_3': -8520.007707566137, 'ele_2_4': 166.4148155968816, 'ele_3_3': 25246.12078642519, 'ele_3_4': -896.3193341158011, 'ele_4_4': 378.3135537330606}
initialized
initialized
initialized
initialized
initialized
initial


 Consider M =
 [[ 5.41154971e+03 -2.76783129e+00 -4.03915113e+03  1.07090070e+04
  -4.82938924e+02]
 [-2.76783129e+00  5.07321594e+00  7.51682148e+00  4.86303914e+01
  -9.98333214e+00]
 [-4.03915113e+03  7.51682148e+00  3.24300911e+03 -8.30939363e+03
   1.62184105e+02]
 [ 1.07090070e+04  4.86303914e+01 -8.30939363e+03  2.46050065e+04
  -8.63544848e+02]
 [-4.82938924e+02 -9.98333214e+00  1.62184105e+02 -8.63544848e+02
   3.61138594e+02]]
[5411.549714304638, -2.7678312875391877, -4039.1511338724936, 10709.007010596531, -482.93892430553035, 5.073215943328396, 7.516821483989252, 48.63039136663165, -9.98333213843224, 3243.009113232682, -8309.39362809683, 162.18410508134838, 24605.00647889857, -863.5448478594144, 361.13859431150604]
   logdet =  28.218792463203993 

Eigvals: [3.23515135e+04 7.96946683e+02 4.28878515e+02 4.48053607e+01
 3.63310303e+00]

 Consider M =
 [[ 5.41272573e+03 -2.76897326e+00 -4.04005006e+03  1.07114041e+04
  -4.82999275e+02]
 [-2.76897326e+00  5.07411062e+00  7.519


 Consider M =
 [[ 5.54616605e+03 -2.95438695e+00 -4.14174322e+03  1.09757574e+04
  -4.93314463e+02]
 [-2.95438695e+00  5.18362769e+00  7.68787880e+00  4.95105048e+01
  -1.01547790e+01]
 [-4.14174322e+03  7.68787880e+00  3.32447568e+03 -8.51898010e+03
   1.66773067e+02]
 [ 1.09757574e+04  4.95105048e+01 -8.51898010e+03  2.52072965e+04
  -8.82165085e+02]
 [-4.93314463e+02 -1.01547790e+01  1.66773067e+02 -8.82165085e+02
   3.67814639e+02]]
[5546.166053450422, -2.954386954894084, -4141.743223431337, 10975.757413629557, -493.3144634195805, 5.183627691232607, 7.687878802461584, 49.51050479243286, -10.15477901495132, 3324.475676097702, -8518.980104638207, 166.77306658389375, 25207.29651610482, -882.1650849058714, 367.81463895478095]
   logdet =  28.317653823995606 

Eigvals: [3.31510498e+04 8.14418652e+02 4.36341571e+02 4.54124239e+01
 3.71410798e+00]

 Consider M =
 [[ 5.54616889e+03 -2.95425520e+00 -4.14174393e+03  1.09757634e+04
  -4.93318312e+02]
 [-2.95425520e+00  5.18364582e+00  7.6878


 Consider M =
 [[ 5.54718927e+03 -2.88685593e+00 -4.14180662e+03  1.09782296e+04
  -4.95274563e+02]
 [-2.88685593e+00  5.19021722e+00  7.67536372e+00  4.97289847e+01
  -1.02798290e+01]
 [-4.14180662e+03  7.67536372e+00  3.32437098e+03 -8.51910752e+03
   1.67062510e+02]
 [ 1.09782296e+04  4.97289847e+01 -8.51910752e+03  2.52148527e+04
  -8.86952833e+02]
 [-4.95274563e+02 -1.02798290e+01  1.67062510e+02 -8.86952833e+02
   3.70793176e+02]]
[5547.189269893196, -2.886855929334754, -4141.806621587034, 10978.22962207939, -495.2745628785312, 5.19021721843767, 7.675363722751035, 49.7289847025316, -10.279828982269873, 3324.370984751833, -8519.107516299007, 167.06251023251167, 25214.852665812374, -886.9528329987058, 370.7931758812699]
   logdet =  28.32655159131149 

Eigvals: [3.31589725e+04 8.14989550e+02 4.39259989e+02 4.54591422e+01
 3.71508761e+00]

 Consider M =
 [[ 5.54734496e+03 -2.88033118e+00 -4.14183287e+03  1.09785309e+04
  -4.95466262e+02]
 [-2.88033118e+00  5.19071672e+00  7.6751151


 Consider M =
 [[ 5.54795873e+03 -2.85537626e+00 -4.14182567e+03  1.09803110e+04
  -4.96234022e+02]
 [-2.85537626e+00  5.18494436e+00  7.70076259e+00  4.97654719e+01
  -1.03385951e+01]
 [-4.14182567e+03  7.70076259e+00  3.32441802e+03 -8.51905511e+03
   1.67085815e+02]
 [ 1.09803110e+04  4.97654719e+01 -8.51905511e+03  2.52208489e+04
  -8.89663182e+02]
 [-4.96234022e+02 -1.03385951e+01  1.67085815e+02 -8.89663182e+02
   3.72360442e+02]]
[5547.958730202141, -2.8553762568977605, -4141.825666643836, 10980.310993799832, -496.2340220880887, 5.184944361169178, 7.700762586262772, 49.76547185397265, -10.338595121695997, 3324.418018689961, -8519.055112496895, 167.08581460498448, 25220.84889836543, -889.6631818040344, 372.36044188349683]
   logdet =  28.331841824210308 

Eigvals: [3.31651814e+04 8.15416309e+02 4.40885638e+02 4.55790819e+01
 3.70859383e+00]

 Consider M =
 [[ 5.54802228e+03 -2.85744014e+00 -4.14178322e+03  1.09805772e+04
  -4.96251476e+02]
 [-2.85744014e+00  5.18091648e+00  7.71

...


 Consider M =
 [[ 5.54366659e+03 -3.06034586e+00 -4.14131256e+03  1.09760452e+04
  -4.91619603e+02]
 [-3.06034586e+00  5.13117489e+00  7.81888840e+00  4.91531782e+01
  -1.01459741e+01]
 [-4.14131256e+03  7.81888840e+00  3.32330180e+03 -8.51584955e+03
   1.67049057e+02]
 [ 1.09760452e+04  4.91531782e+01 -8.51584955e+03  2.52167573e+04
  -8.84307008e+02]
 [-4.91619603e+02 -1.01459741e+01  1.67049057e+02 -8.84307008e+02
   3.65376186e+02]]
[5543.666589912874, -3.0603458598316675, -4141.312559395046, 10976.045246224752, -491.6196029112913, 5.131174891198286, 7.818888401312216, 49.15317821883658, -10.145974128514549, 3323.3018038366154, -8515.849551083522, 167.04905696710543, 25216.75727963972, -884.3070083558487, 365.37618595731846]
   logdet =  28.29277540865243 

Eigvals: [3.31562218e+04 8.16127931e+02 4.33160003e+02 4.50529989e+01
 3.67029446e+00]

 Consider M =
 [[ 5.54379560e+03 -3.05528105e+00 -4.14132814e+03  1.09762953e+04
  -4.91760803e+02]
 [-3.05528105e+00  5.13121715e+00  7.81


 Consider M =
 [[ 5.54685211e+03 -2.93353585e+00 -4.14143314e+03  1.09812566e+04
  -4.94609347e+02]
 [-2.93353585e+00  5.13260751e+00  7.86389874e+00  4.92874149e+01
  -1.02720372e+01]
 [-4.14143314e+03  7.86389874e+00  3.32384826e+03 -8.51658291e+03
   1.66963284e+02]
 [ 1.09812566e+04  4.92874149e+01 -8.51658291e+03  2.52267575e+04
  -8.89657545e+02]
 [-4.94609347e+02 -1.02720372e+01  1.66963284e+02 -8.89657545e+02
   3.69950108e+02]]
[5546.852108011926, -2.9335358451034472, -4141.433138123291, 10981.256648840714, -494.60934711007195, 5.1326075144411405, 7.863898740518713, 49.28741492269755, -10.272037235084827, 3323.848255523123, -8516.582914370305, 166.96328370950724, 25226.757457557673, -889.6575446520595, 369.95010812392275]
   logdet =  28.31627027073069 

Eigvals: [3.31686236e+04 8.16375679e+02 4.38275909e+02 4.55985726e+01
 3.66676917e+00]

 Consider M =
 [[ 5.54705632e+03 -2.92378269e+00 -4.14142564e+03  1.09815664e+04
  -4.94796450e+02]
 [-2.92378269e+00  5.13288490e+00  7.


 Consider M =
 [[ 5.54825908e+03 -2.89384668e+00 -4.14141807e+03  1.09832571e+04
  -4.95933966e+02]
 [-2.89384668e+00  5.13530303e+00  7.85514144e+00  4.94116817e+01
  -1.03206129e+01]
 [-4.14141807e+03  7.85514144e+00  3.32432540e+03 -8.51759262e+03
   1.66905877e+02]
 [ 1.09832571e+04  4.94116817e+01 -8.51759262e+03  2.52324245e+04
  -8.91847470e+02]
 [-4.95933966e+02 -1.03206129e+01  1.66905877e+02 -8.91847470e+02
   3.71942901e+02]]
[5548.259081569297, -2.8938466812322323, -4141.418071166609, 10983.257077244107, -495.93396647150166, 5.135303030538749, 7.85514144264832, 49.41168169001603, -10.320612883277517, 3324.3254030675726, -8517.592617720116, 166.90587700575986, 25232.42452265411, -891.847469831494, 371.94290136381414]
   logdet =  28.329573391397346 

Eigvals: [3.31751966e+04 8.16685151e+02 4.40598486e+02 4.59402701e+01
 3.66667730e+00]

 Consider M =
 [[ 5.54835337e+03 -2.89149450e+00 -4.14141416e+03  1.09833833e+04
  -4.96017992e+02]
 [-2.89149450e+00  5.13525409e+00  7.85


 Consider M =
 [[ 5.54921149e+03 -2.87060161e+00 -4.14133586e+03  1.09845238e+04
  -4.96920677e+02]
 [-2.87060161e+00  5.13660754e+00  7.84785984e+00  4.94906458e+01
  -1.03561772e+01]
 [-4.14133586e+03  7.84785984e+00  3.32468307e+03 -8.51826572e+03
   1.66775348e+02]
 [ 1.09845238e+04  4.94906458e+01 -8.51826572e+03  2.52361633e+04
  -8.93298548e+02]
 [-4.96920677e+02 -1.03561772e+01  1.66775348e+02 -8.93298548e+02
   3.73429612e+02]]
[5549.211485322725, -2.8706016098019935, -4141.335860022494, 10984.523761909642, -496.92067669535237, 5.1366075389344985, 7.847859840901026, 49.490645751916595, -10.356177236787122, 3324.683072129474, -8518.265722433924, 166.77534777357104, 25236.16331927813, -893.2985484666654, 373.42961238297084]
   logdet =  28.33878804175996 

Eigvals: [3.31794929e+04 8.16895652e+02 4.42407141e+02 4.61620005e+01
 3.66636916e+00]

 Consider M =
 [[ 5.54942187e+03 -2.85725244e+00 -4.14133998e+03  1.09848350e+04
  -4.97150880e+02]
 [-2.85725244e+00  5.13927068e+00  7.


 Consider M =
 [[ 5.55085988e+03 -2.77224751e+00 -4.14125211e+03  1.09865945e+04
  -4.98754671e+02]
 [-2.77224751e+00  5.15589748e+00  7.83371770e+00  4.96925470e+01
  -1.04335501e+01]
 [-4.14125211e+03  7.83371770e+00  3.32499161e+03 -8.51871517e+03
   1.66472328e+02]
 [ 1.09865945e+04  4.96925470e+01 -8.51871517e+03  2.52400920e+04
  -8.95153265e+02]
 [-4.98754671e+02 -1.04335501e+01  1.66472328e+02 -8.95153265e+02
   3.76015279e+02]]
[5550.859884267742, -2.772247512792839, -4141.252114892028, 10986.594506666092, -498.7546711067911, 5.155897482799525, 7.83371770157092, 49.69254703298534, -10.43355005088689, 3324.9916102471543, -8518.71516764063, 166.47232810914846, 25240.09204163831, -895.1532646297595, 376.0152786889015]
   logdet =  28.353005828749154 

Eigvals: [3.31845041e+04 8.17034477e+02 4.45602720e+02 4.62927850e+01
 3.68058726e+00]

 Consider M =
 [[ 5.55107046e+03 -2.75725868e+00 -4.14124889e+03  1.09868274e+04
  -4.98981171e+02]
 [-2.75725868e+00  5.15918959e+00  7.830790

In [86]:
fim_result = np.zeros((5,5))
for i in range(5):
    for j in range(i,5):
        fim_result[i,j] = fim_result[j,i] = pyo.value(mod.TotalFIM[i,j])
        
print(fim_result)  
print('trace:', np.trace(fim_result))
print('det:', np.linalg.det(fim_result))
print(np.linalg.eigvals(fim_result))

print("Pyomo OF:", pyo.value(mod.Obj))
print("Log_det:", np.log(np.linalg.det(fim_result)))

[[ 5.55157638e+03 -2.71917041e+00 -4.14125658e+03  1.09873693e+04
  -4.99513645e+02]
 [-2.71917041e+00  5.16755719e+00  7.82299238e+00  4.97984728e+01
  -1.04565254e+01]
 [-4.14125658e+03  7.82299238e+00  3.32507933e+03 -8.51891141e+03
   1.66356911e+02]
 [ 1.09873693e+04  4.97984728e+01 -8.51891141e+03  2.52406039e+04
  -8.95688936e+02]
 [-4.99513645e+02 -1.04565254e+01  1.66356911e+02 -8.95688936e+02
   3.77340454e+02]]
trace: 34499.76759257504
det: 2074289159688.2432
[3.31856857e+04 8.16909682e+02 4.47098716e+02 4.63839120e+01
 3.68955222e+00]
Pyomo OF: 28.360639639149042
Log_det: 28.360639637275234


In [87]:
ans_y, sol_y = calculator.extract_solutions(mod)

Ads.gas_inlet.F :  1.0
Ads.gas_outlet.F :  0.6
Ads.gas_outlet.T :  1.0
Des.gas_inlet.F :  1.0
Des.gas_outlet.F :  1.0
Des.gas_outlet.T :  1.0
Ads.T_g.Value(19,10) :  1.0
Ads.T_g.Value(23,10) :  1.0
Ads.T_g.Value(28,10) :  1.0
Ads.gas_outlet.z("CO2").static :  1.0
Des.gas_outlet.z("CO2").static :  1.0
Ads.gas_outlet.z("CO2").dynamic
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
Des.gas_outlet.z("CO2").dynamic
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1. 0. 0. 0. 0. 1.
 0. 0.

In [88]:
for i in range(5):
    print(all_names_strategy3[i+11])
    for t in range(len(sol_y[0])):
        if sol_y[i][t] > 0.95:
            print(dynamic_time_dict[t])

Ads.gas_outlet.z("CO2").dynamic
104.0
114.0
124.0
134.0
182.0
Des.gas_outlet.z("CO2").dynamic
162.0
172.0
182.0
192.0
202.0
Ads.z("CO2",19,10)
94.0
Ads.z("CO2",23,10)
96.0
Ads.z("CO2",28,10)
88.0
98.0
108.0
118.0
174.0


In [89]:
# verify cost 
#real_cost = 0 
#for i in range(num_total):
#    real_cost += ans_y[i,i]*cost[i]
    
#dynamic_inst = []
#for j in range(num_static, num_dynamic+num_static):
#    dynamic_inst.append(pyo.value(mod.if_install_dynamic[j]))
#    for t in range(Nt):
#        if sol_y[j,t]>0.99:
#            dynamic_inst[j] = 1 
            
#real_cost += sum(dynamic_inst[i]*install_cost_dynamic[i] for i in range(num_dynamic))
#print(dynamic_inst)
#print('Real cost:', real_cost)
print('pyomo calculated cost:', pyo.value(mod.cost))

pyomo calculated cost: 25000.000099620884


In [90]:
count = 0 
for i in range(561):
    for j in range(i,561):
        #if pyo.value(mod.cov_y[i,j])<0.96:
        print(pyo.value(mod.cov_y[i,j]))
            #count += 1 
            
print(count)

0.9999999799790927
0.5999084288694688
0.9999997907717727
0.9999995006807942
0.9999999501899755
0.9999999701582786
0.999999984244301
0.9999981563736462
0.9999999700617047
0.9999999560239822
0.9999998121611443
3.893713711495985e-06
3.8929721367778045e-06
3.88051675885562e-06
3.865635318219512e-06
3.8509164525585986e-06
3.839584662266851e-06
3.837250994399764e-06
3.848777795171054e-06
3.883715222032857e-06
3.930847996381612e-06
3.972045614619214e-06
4.01678674234922e-06
4.064111833953384e-06
4.105445857433539e-06
4.140117460897086e-06
4.165329554310377e-06
4.1813746612810775e-06
4.18782073869959e-06
4.185496592464139e-06
4.17482940164617e-06
4.154832709232119e-06
4.129383292477863e-06
4.100285546660679e-06
4.066990882045782e-06
4.033367497723008e-06
3.999393590242822e-06
3.965587865702657e-06
3.9308148729291006e-06
3.899067543688729e-06
3.869225156010857e-06
3.841362852697361e-06
3.8146480976317826e-06
3.791791793256518e-06
3.764658631889306e-06
3.7367395283972936e-06
3.7141784441189024e-

3.8745748891131755e-06
4.112363324660848e-06
4.475161615761722e-06
5.074464747188778e-06
6.2825230511180004e-06
9.23826034905382e-06
2.45916419794676e-05
6.879207871129131e-05
0.0004236777058123152
0.9991337979185169
0.00031170508862399856
6.0792168631788976e-05
6.879741855346999e-05
0.0004236797460733326
0.9991337983093455
0.00031170611662826794
6.079598515253739e-05
6.87970473253936e-05
0.0004236800305040594
0.9991337978226889
0.0003117060251060272
6.0795579958258274e-05
6.87927974692544e-05
0.0004236786854478992
0.9991337963378873
0.0003117053960482773
6.078024043304882e-05
2.0981102682729854e-05
9.735157708170227e-06
6.8802150588348916e-06
5.49754701308067e-06
4.770144753383396e-06
4.3097890983547525e-06
4.001713814573545e-06
3.782996456964334e-06
3.6466469603895496e-06
3.55867742307764e-06
3.4972299579926103e-06
3.4747678157470695e-06
3.5083968341932466e-06
3.6101446769561463e-06
3.8240479075202014e-06
4.219293202003046e-06
5.05705269595457e-06
7.401400103447002e-06
1.393797508076

6.913166745716315e-06
6.2609927419139745e-06
5.827721051381353e-06
5.7199260220654424e-06
5.430258493024254e-06
5.405971324260322e-06
5.1903860518184115e-06
4.974247996991002e-06
4.908140585322214e-06
4.834865544711175e-06
4.718994769700666e-06
4.7314460883464945e-06
4.625443180435601e-06
4.679556630790065e-06
4.657423149404455e-06
4.613521512304947e-06
4.596573979992443e-06
4.545327996441366e-06
4.5039747490818185e-06
4.4918861675531104e-06
4.37715522315397e-06
4.399992091131438e-06
4.35275066652039e-06
4.3450744062995894e-06
4.310370058833411e-06
4.294364651002017e-06
4.273171318038414e-06
4.23468117093792e-06
4.201334342203038e-06
4.170911326683702e-06
4.1592449645488545e-06
4.144146200599234e-06
4.135671186077901e-06
4.136594553634955e-06
4.1490721073405965e-06
4.167959869975999e-06
4.198956844570441e-06
4.245231743694388e-06
4.281592518085122e-06
4.358676858024261e-06
4.444531090346377e-06
4.503591223778872e-06
4.6263822193210935e-06
4.758570915503635e-06
4.867636100832898e-06
5.0

5.417606752587347e-06
5.202018691576643e-06
4.9858775377362505e-06
4.9197691098776375e-06
4.846492901947235e-06
4.730620187307021e-06
4.743071720214594e-06
4.6370669417181665e-06
4.6911813604514095e-06
4.669047486444605e-06
4.6251450563997165e-06
4.608197212825315e-06
4.556950269979098e-06
4.515596228024051e-06
4.5035074106621804e-06
4.388774144207725e-06
4.411611486874247e-06
4.364369073204704e-06
4.3566926496379565e-06
4.321987554230125e-06
4.305981796170303e-06
4.284787994232699e-06
4.246296979553365e-06
4.2129493824483e-06
4.182525651733256e-06
4.170859011725215e-06
4.155759885100515e-06
4.147284665476581e-06
4.148208055389477e-06
4.160685910526464e-06
4.179574124933811e-06
4.2105718293916775e-06
4.2568477921538705e-06
4.29320938128667e-06
4.370295390299701e-06
4.456151393773466e-06
4.515212695265256e-06
4.638005997643485e-06
4.770197009067365e-06
4.8792639855635235e-06
5.089832479595592e-06
5.327361160258653e-06
5.486232446302984e-06
5.971790092004924e-06
6.3247092870509364e-06
6.

3.367887459824717e-06
3.336742851032677e-06
3.305339851242305e-06
3.273661124339123e-06
3.242192340595481e-06
3.209880174540761e-06
3.180431602022415e-06
3.1527966831894335e-06
3.1270373092845434e-06
3.1023778876072516e-06
3.0813111081414593e-06
3.0563403786152326e-06
3.030690510889661e-06
3.009996686490482e-06
2.9962866140565034e-06
2.9941651623296497e-06
3.0096152409070463e-06
3.046185682966833e-06
3.1100044301333967e-06
3.209055914168487e-06
3.3654542545437897e-06
3.589948721829652e-06
3.935925451217967e-06
4.5140765001249005e-06
5.694535061074945e-06
8.61814220596897e-06
2.393669462397017e-05
6.81257154592558e-05
0.00042300614446325784
0.9991331247950376
0.0003110339688918982
6.012660769706159e-05
6.813105631653187e-05
0.0004230081847200655
0.9991331251858657
0.0003110349968921764
6.0130423783197264e-05
6.813068512214837e-05
0.00042300846915026367
0.9991331246992096
0.00031103490537039884
6.013001863336431e-05
6.81264356418949e-05
0.0004230071240969059
0.9991331232144094
0.00031103

...

1.406327080956545e-06
1.4064148822219919e-06
1.4064893812762415e-06
1.4129288813477918e-06
1.443524125571095e-06
1.4841241878123839e-06
1.5250335612151666e-06
1.5610799115816497e-06
1.5860803238347e-06
1.6038811441944544e-06
1.617077859188561e-06
1.6147173281026351e-06
1.6019130777285845e-06
1.5851972153197687e-06
1.5660422861752573e-06
1.5445697114534764e-06
1.523765360490927e-06
1.5036799056466054e-06
1.4842615774407267e-06
1.4679335379669948e-06
1.4539769324445984e-06
1.4424110415561661e-06
1.4327225260310785e-06
1.4256093423301804e-06
1.420337785701154e-06
1.4166243847227402e-06
1.4141257368689134e-06
1.4129292492603218e-06
1.4126743716663629e-06
1.4131451135784533e-06
1.4142337287789026e-06
1.4156544066656873e-06
1.4172987359292542e-06
1.419073526757438e-06
2.2280541897069714e-06
1.405402032429402e-06
1.4058490198298867e-06
1.409066416889257e-06
1.418675225295561e-06
1.4432814473529679e-06
1.4911308519048059e-06
1.5677787094396357e-06
1.6071273999569323e-06
1.61244765797131e-06
1.

1.9836050839953068e-06
1.9978256887092467e-06
2.0040231963733633e-06
1.9969351977502247e-06
1.977474002217522e-06
1.9836061654181473e-06
1.9978256733481738e-06
2.004023195074113e-06
1.9969351644339354e-06
1.9774755537025527e-06
1.9836063523072393e-06
1.9978256131768455e-06
2.0040231895408313e-06
1.9969351393708776e-06
1.9774777277293635e-06
1.983606636427289e-06
1.9978254772258246e-06
2.004023182243185e-06
1.9969351160503783e-06
1.9774810626561594e-06
1.9836068326762967e-06
1.9978231377932016e-06
1.8901802981912385e-06
1.7768300721154e-06
1.687123889296825e-06
1.6206440954022083e-06
1.5740481610316377e-06
1.541019232418384e-06
1.5200184273152215e-06
1.506376192023692e-06
1.497819381944835e-06
1.4929705017899882e-06
1.4908576565059693e-06
1.4901087593303094e-06
1.4900287058667607e-06
1.4901708471865026e-06
1.4903218075576068e-06
1.490449931287173e-06
1.5016459514573365e-06
1.5584403567102444e-06
1.6447519801967613e-06
1.746457946405106e-06
1.8467374461217831e-06
1.9183198553387476e-06
1

1.6716430292933685e-06
1.6540070988572345e-06
1.6420159631565572e-06
1.634137052752246e-06
1.6304162513261097e-06
1.6296279114969557e-06
1.6310850912286224e-06
1.6344745233358157e-06
1.6389396717555967e-06
1.64416811723559e-06
1.6498858505325281e-06
2.2841265883008895e-05
9.203131948885506e-06
1.13958519453647e-05
1.2165528519085e-05
1.1273759349563479e-05
8.27760326240489e-06
9.203176876719963e-06
1.1395833569577778e-05
1.216552760843405e-05
1.1273756110495299e-05
8.278077621537728e-06
9.203207909596413e-06
1.139551740397998e-05
3.51274102491544e-06
2.4111293310924505e-06
2.044818498432391e-06
1.8624521201616913e-06
1.7587814742602343e-06
1.6935818631201086e-06
1.6549630132003316e-06
1.6308979108132348e-06
1.6161794136713706e-06
1.6079607295590755e-06
1.6044062681961818e-06
1.603150228357965e-06
1.6030160819601846e-06
1.6032542852976546e-06
1.6035073464908346e-06
1.6037221893279876e-06
1.622726954304072e-06
1.7272333605445093e-06
1.922992828273804e-06
2.264254791831609e-06
2.924646418

3.011600144330579e-06
4.442195956342572e-06
8.714917159743394e-06
6.75557229819656e-05
3.829603318886458e-05
7.752637965469951e-06
4.3539337780165225e-06
3.1855149595496973e-06
2.6007043787770332e-06
2.2838030248967834e-06
2.0827745059551905e-06
1.9419154886394365e-06
1.8489349852362277e-06
1.782277045940328e-06
1.7338441268029216e-06
1.6971140566761555e-06
1.6720462791585342e-06
1.654389564704742e-06
1.6423846170847771e-06
1.6344967721382298e-06
1.6307717901701554e-06
1.6299825677985433e-06
1.6314413797542808e-06
1.634834623183458e-06
1.6393048240360847e-06
1.6445392311793116e-06
1.650263540306301e-06
6.403937130238969e-06
2.213056888840956e-06
1.9436710983271263e-06
1.796128165365731e-06
1.7085662482422578e-06
1.6522002589064251e-06
1.618357818933342e-06
1.597101521444219e-06
1.5840384206824244e-06
1.5767236402442503e-06
1.5735555864462907e-06
1.5724354407969396e-06
1.5723157879822566e-06
1.5725282524437294e-06
1.5727539559312055e-06
1.572945561917032e-06
1.589855378064518e-06
1.6814

1.415680160187519e-06
1.4174347910653468e-06
2.2247341056811437e-06
1.4049983207349437e-06
1.405072061946949e-06
1.411445039136284e-06
1.4416970337852815e-06
1.4817768070788856e-06
1.5221036746565418e-06
1.5576128864097053e-06
1.5822433053542916e-06
1.599788715290253e-06
1.6128029655291606e-06
1.610474567587745e-06
1.597848414113631e-06
1.5813730872789484e-06
1.5625012020442098e-06
1.5413496326531111e-06
1.5208541361924685e-06
1.5010597704871823e-06
1.4819123247462872e-06
1.4658018026033068e-06
1.4520225740971032e-06
1.4405972100098811e-06
1.431021686308749e-06
1.423988645447e-06
1.4187749231226161e-06
1.4151014592314298e-06
1.4126293091668826e-06
1.4114454031815105e-06
1.4111931967873426e-06
1.4116590027065243e-06
1.412736162075541e-06
1.414141803486314e-06
1.415768607321691e-06
1.4175243357503054e-06
2.2252557201347324e-06
1.4051590714096679e-06
1.41153611879204e-06
1.4418090965028575e-06
1.481920622295552e-06
1.5222829809182222e-06
1.5578248872121037e-06
1.5824778220456245e-06
1.600

In [91]:
store = True

if store:
    file = open('Mar31_D_110_25000', 'wb')

    pickle.dump(ans_y, file)

    file.close()
    
    file2 = open('Mar31_FIM_D_110_25000', 'wb')

    pickle.dump(fim_result, file2)

    file2.close()